In [14]:

from llama_index.readers.obsidian import ObsidianReader
import openai
from llama_index.core.memory.chat_memory_buffer import MessageRole
from llama_index.core import SimpleDirectoryReader, KnowledgeGraphIndex, VectorStoreIndex
from llama_index.core.graph_stores import SimpleGraphStore
from llama_index.core.storage.docstore import SimpleDocumentStore
from llama_index.core import Document, PropertyGraphIndex
from llama_index.core.storage.index_store import SimpleIndexStore
from llama_index.core.vector_stores import SimpleVectorStore
from llama_index.core import Settings
from IPython.display import Markdown, display
from llama_index.llms.ollama import Ollama
from tqdm.notebook import tqdm
import time
import os
from llama_index.core.llms import ChatMessage
from llama_index.core import StorageContext
from llama_index.llms.ollama import Ollama
from llama_index.embeddings.ollama import OllamaEmbedding
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.llms.openai import OpenAI
from llama_index.core.memory import ChatMemoryBuffer
import logging
import sys
import ipywidgets as widgets
import json
from llama_index.core.callbacks import CallbackManager
from llama_index.core.callbacks import LlamaDebugHandler
from llama_index.core import ServiceContext
from llama_index.core.query_engine import RetrieverQueryEngine
from llama_index.core.retrievers import KnowledgeGraphRAGRetriever
from llama_index.core.indices.property_graph import (
    SimpleLLMPathExtractor,
    SchemaLLMPathExtractor,
    DynamicLLMPathExtractor,
)
import yaml
from dotenv import load_dotenv

In [15]:
from llama_index.core import (
    load_index_from_storage,
    load_indices_from_storage,
    load_graph_from_storage,
)

In [16]:
import nest_asyncio

nest_asyncio.apply()

In [17]:
logging.basicConfig(stream=sys.stdout, level=logging.INFO)
logging.getLogger().addHandler(logging.StreamHandler(stream=sys.stdout))

# Build a simple directory

In [18]:
simple_glossary = SimpleDirectoryReader(
    r"/Users/arthursarazin/Documents/coreandgraphs/graphandopenmodels/graph"
).load_data()

# Upload Obsidian vault files

#### Using Obsidian reader from LLama Index

In [19]:
#locate obsidian files that make your graph
filepath = r"/Users/arthursarazin/Documents/coreandgraphs/graphandopenmodels/graph"

#load the graph files 
graph_files = ObsidianReader(filepath).load_data()
print(list(graph_files))

[Document(id_='94aa8c61-0047-4de5-88cd-499a3f1fce52', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, metadata_template='{key}: {value}', metadata_separator='\n', text_resource=MediaResource(embeddings=None, data=None, text="Quels critères pour dire que des données sont de qualité ?\n- Exactitude : les données sont justes et cohérentes\n- Complétude : le jeu de données est complet \n- Pertinence : les données que l'on a sont elles pertinentes pour répondre à nos besoins (et par extension ceux du client ?)\n\nDes données de bonnes qualités sont essentielles pour avoir des donnes fiables ", mimetype=None, path=None, url=None), image_resource=None, audio_resource=None, video_resource=None, text_template='{metadata_str}\n\n{content}'), Document(id_='60834fc7-e47f-431a-9b13-c333d88d4faa', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, metadata_template='{key}: {valu

# Using manual code to create specific ontology

In [20]:
# Fonction pour extraire les métadonnées YAML et le titre d'un fichier Markdown
def extract_metadata_and_title(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        content = f.read()
        # Recherchez la section YAML (entre `---` au début et à la fin)
        if content.startswith("---"):
            try:
                yaml_block = content.split("---", 2)[1]
                metadata = yaml.safe_load(yaml_block)
                return os.path.basename(file_path).replace(".md", ""), metadata
            except Exception as e:
                print(f"Erreur lors de l'extraction des métadonnées de {file_path}: {e}")
                return None, None
        return os.path.basename(file_path).replace(".md", ""), None

# Parcourir les fichiers Obsidian et créer des entités et relations
def process_obsidian_notes(directory):
    entities = []
    relations = []
    
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith(".md"):
                file_path = os.path.join(root, file)
                title, metadata = extract_metadata_and_title(file_path)
                if title:
                    # Ajouter l'entité basée sur le titre
                    entities.append({"name": title})
                    
                    # Ajouter les relations basées sur les propriétés YAML
                    if metadata:
                        for key, value in metadata.items():
                            relations.append({
                                "type": key,  # Nom de la propriété comme relation
                                "source": title,  # Titre du fichier comme entité source
                                "target": value,  # Valeur de la propriété comme entité cible
                            })
    return entities, relations



In [21]:
# Exemple d'utilisation
obsidian_dir = r"C:\Users\asarazin\OneDrive - Veltys Max\Documents\documente-marcel\graph"
entities, relations = process_obsidian_notes(obsidian_dir)

print(relations)

[]


# Set LLM (OpenAI)

In [22]:
load_dotenv()  # Charge les variables depuis le fichier .env
api_key = os.getenv("OPENAI_API_KEY_UP")
# Modifier ou ajouter une variable d'environnement
os.environ["OPENAI_API_KEY"] = api_key

In [23]:
llm = OpenAI(temperature=0, model="gpt-4o", max_tokens=3000)
Settings.llm = llm
Settings.chunk_size = 512

# Set local LLM for embeddings ()

In [24]:
# bge-base embedding model
Settings.embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-base-en-v1.5")
#Settings.embed_model = OpenAIEmbedding(model="text-embedding-3-small")


INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']


# Set LLM for chat  (Local)

In [25]:
#llm = Ollama(model="tinyllama", request_timeout=120.0)
#Settings.llm = llm
#Settings.chunk_size = 512

# Test LLM

In [26]:
messages = [
    ChatMessage(
        role="system", content="You are a data governance consultant"
    ),
    ChatMessage(role="user", content="What's your favorite data tool ?"),
]
resp = llm.chat(messages)
print(resp)

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
assistant: As a data governance consultant, I don't have personal preferences or feelings. However, I can provide insights into popular data tools that are widely used in the industry. Some of the most commonly used data governance tools include:

1. **Collibra**: Known for its comprehensive data governance platform that helps organizations manage data assets, ensure compliance, and improve data quality.

2. **Informatica**: Offers a suite of data governance tools that include data cataloging, data quality, and master data management to help organizations manage their data effectively.

3. **Alation**: Provides a data cataloging solution that helps organizations discover, understand, and manage their data assets.

4. **Talend**: Offers dat

In [27]:
# Instantiate vector store
simple_glossary = SimpleDirectoryReader(
    r"/Users/arthursarazin/Documents/coreandgraphs/graphandopenmodels/graph"
)

# Instantiate graph store 

In [28]:
graph_store = SimpleGraphStore()
graph_storage_context = StorageContext.from_defaults(graph_store=graph_store)

# Instantiate ontology store

In [29]:
onto_store = SimpleGraphStore()
onto_storage_context = StorageContext.from_defaults(graph_store=onto_store)

# Construct Index

## Construct Vector Store Index

In [30]:
vector_index = VectorStoreIndex.from_documents(
    documents = simple_glossary.load_data(),
    show_progress=True)

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/44 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [31]:
# save index to disk
vector_index.set_index_id("vector_index")
vector_index.storage_context.persist("vector")

## Construct knowledge graph index 

In [32]:
def process_document(doc):
    # This function will be called for each document
    print(f"Processing document: {doc.doc_id}")
    return doc

In [33]:
# Assuming you have your graph files loaded
print(f"Starting to process {len(graph_files)} documents...")

Starting to process 44 documents...


In [34]:
# Wrap your document processing in a progress bar
graph_index = KnowledgeGraphIndex.from_documents(
        documents=[process_document(doc) for doc in graph_files],  # process one document at a time
        max_triplets_per_chunk=2,
        storage_context=graph_storage_context,
        include_embeddings=True,
    show_progress=True,
)


Processing document: 94aa8c61-0047-4de5-88cd-499a3f1fce52
Processing document: 60834fc7-e47f-431a-9b13-c333d88d4faa
Processing document: 07dc122c-562a-4fc4-98c0-049b8d65d3b6
Processing document: f4da346f-ee06-44a3-95f4-cdfeb477c0db
Processing document: eab92812-04a2-40df-aaee-06580943afb8
Processing document: 186de23b-f919-48cc-a997-7bfd3404bea9
Processing document: a81fb86a-d6b7-4272-a39c-94cf16aacf56
Processing document: b73e8ce5-af9c-4ab9-a838-32834241f4c9
Processing document: 92778ed6-de1f-4f96-9ed5-e14de87a5b9a
Processing document: ee6fe1e5-a396-421f-a6a1-6135d915a241
Processing document: 03cba372-62c1-4d5f-9cba-4aa04db2b3b5
Processing document: a482c755-2275-4ba7-8179-63ad3f14f03a
Processing document: 414cfedd-90ab-4b86-b801-60e2f7e9f079
Processing document: ca5c709d-2e82-4a1e-b625-35a2d8ce8e9f
Processing document: 4bc3ca02-948d-4dce-8e3d-b758b7c257c4
Processing document: bbb23bb7-cf93-4eca-ad6e-6f222254bd7a
Processing document: bd6f7087-ecb6-44f8-a5cd-a571e4e5a8f8
Processing doc

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Processing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

...

Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [35]:
print(graph_index)

In [36]:
graph_index.set_index_id("graph_index")
graph_index.storage_context.persist("knowledge_graph")
graph_storage_context.persist(persist_dir="knowledge_graph")


## Construct knowledge with ontology as assistant

In [37]:
onto_store = SimpleGraphStore()
onto_storage_context = StorageContext.from_defaults(graph_store=onto_store)

In [38]:
# Configurer DynamicLLMPathExtractor avec les entités et relations extraites
kg_extractor = DynamicLLMPathExtractor(
    llm=llm,
    max_triplets_per_chunk=20,
    num_workers=4,
    allowed_entity_types=None,  # Si vous ne limitez pas les types d'entités
    allowed_relation_types=None,  # Si vous ne limitez pas les types de relations
    allowed_entity_props=None,
    allowed_relation_props=None,
)

In [39]:
# Résumé des entités et relations extraites
print("Entités :")
for entity in entities:
    print(entity)

print("\nRelations :")
for relation in relations:
    print(relation)

Entités :

Relations :


In [40]:
onto_index = PropertyGraphIndex.from_documents(
    documents=[process_document(doc) for doc in graph_files],
    llm=llm,
    storage_context=onto_storage_context,
    embed_kg_nodes=True,
    kg_extractors=[kg_extractor],
    show_progress=True,
    graph_store=onto_store 

)

Processing document: 94aa8c61-0047-4de5-88cd-499a3f1fce52
Processing document: 60834fc7-e47f-431a-9b13-c333d88d4faa
Processing document: 07dc122c-562a-4fc4-98c0-049b8d65d3b6
Processing document: f4da346f-ee06-44a3-95f4-cdfeb477c0db
Processing document: eab92812-04a2-40df-aaee-06580943afb8
Processing document: 186de23b-f919-48cc-a997-7bfd3404bea9
Processing document: a81fb86a-d6b7-4272-a39c-94cf16aacf56
Processing document: b73e8ce5-af9c-4ab9-a838-32834241f4c9
Processing document: 92778ed6-de1f-4f96-9ed5-e14de87a5b9a
Processing document: ee6fe1e5-a396-421f-a6a1-6135d915a241
Processing document: 03cba372-62c1-4d5f-9cba-4aa04db2b3b5
Processing document: a482c755-2275-4ba7-8179-63ad3f14f03a
Processing document: 414cfedd-90ab-4b86-b801-60e2f7e9f079
Processing document: ca5c709d-2e82-4a1e-b625-35a2d8ce8e9f
Processing document: 4bc3ca02-948d-4dce-8e3d-b758b7c257c4
Processing document: bbb23bb7-cf93-4eca-ad6e-6f222254bd7a
Processing document: bd6f7087-ecb6-44f8-a5cd-a571e4e5a8f8
Processing doc

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Extracting and inferring knowledge graph from text:   0%|          | 0/44 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Extracting and inferring knowledge graph from text:   2%|▏         | 1/44 [00:01<00:55,  1.29s/it]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings: 100%|██████████| 44/44 [00:40<00:00,  1.09it/s]


In [41]:
print(onto_storage_context)

StorageContext(docstore=<llama_index.core.storage.docstore.simple_docstore.SimpleDocumentStore object at 0x2b28d8970>, index_store=<llama_index.core.storage.index_store.simple_index_store.SimpleIndexStore object at 0x2b28da9b0>, vector_stores={'default': SimpleVectorStore(stores_text=False, is_embedding_query=True, data=SimpleVectorStoreData(embedding_dict={'Exactitude': [0.007702469825744629, 0.010833575390279293, 0.05388922616839409, -0.01903216913342476, 0.013069759123027325, 0.061195164918899536, 0.04388252645730972, 0.030481679365038872, -0.03302859514951706, -0.013718584552407265, -0.007305257022380829, 0.019380634650588036, -0.06734344363212585, 0.028604838997125626, -0.03636658191680908, 0.07862746715545654, 0.06451626867055893, -0.010957726277410984, -0.007658907677978277, -0.012740922160446644, 0.01193417888134718, -0.009854189120233059, -0.02950836904346943, -0.022641027346253395, 0.0029550674371421337, 0.011440406553447247, 0.003733488265424967, -0.02187698893249035, -0.073

In [42]:
# save index to disk
onto_index.set_index_id("onto_index")
onto_index.storage_context.persist("onto_graph")
onto_storage_context.persist(persist_dir="onto_graph")